In [1]:
%%bash
docker-compose up -d influxdb

influxdb is up-to-date


In [2]:
import requests
requests.post(url="http://localhost:8086/query", params={'q':'CREATE DATABASE "mydb"'})

<Response [200]>

In [3]:
p = "foo bar=NaN"
r = requests.post(url="http://localhost:8086/write?db=mydb", data=p)
r.text

'{"error":"unable to parse \'foo bar=NaN\': invalid number"}\n'

In [4]:
p1 = "foo bar=1.0,baz=1.0"
p2 = "foo baz=2.0"
p3 = "foo bar=3.0,baz=3.0"
requests.post(url="http://localhost:8086/write?db=mydb", data=p1)
requests.post(url="http://localhost:8086/write?db=mydb", data=p2)
requests.post(url="http://localhost:8086/write?db=mydb", data=p3)

<Response [204]>

In [5]:
r = requests.get(url="http://localhost:8086/query", params={'q': 'SELECT * FROM "mydb"."autogen"."foo"'})
r.json()['results'][0]['series']

[{'name': 'foo',
  'columns': ['time', 'bar', 'baz'],
  'values': [['2021-03-11T17:07:08.257339123Z', 1, 1],
   ['2021-03-11T17:07:08.271710713Z', None, 2],
   ['2021-03-11T17:07:08.27527696Z', 3, 3]]}]

In [6]:
r = requests.get(url="http://localhost:8086/query", params={'q': 'SELECT mean(baz), mean(baz) FROM "mydb"."autogen"."foo" GROUP BY time(10ms) fill(linear)'})
r.json()['results'][0]['series']

[{'name': 'foo',
  'columns': ['time', 'mean', 'mean_1'],
  'values': [['2021-03-11T17:07:08.25Z', 1, 1],
   ['2021-03-11T17:07:08.26Z', 1.75, 1.75],
   ['2021-03-11T17:07:08.27Z', 2.5, 2.5],
   ['2021-03-11T17:07:08.28Z', None, None],
   ['2021-03-11T17:07:08.29Z', None, None]]}]

In [7]:
from aioinflux import InfluxDBClient
client = InfluxDBClient(db="mydb", output="dataframe")
await client.query('SELECT * FROM foo')

bar  baz
2021-03-11 17:07:08.257339123+00:00  1.0    1
2021-03-11 17:07:08.271710713+00:00  NaN    2
2021-03-11 17:07:08.275276960+00:00  3.0    3